# Using GeoJSON Point Features with Markers

In [39]:
import os
import folium
import geopandas as gpd
import pandas as pd
import datetime

In [115]:
# gdf = gpd.read_file(os.path.join(rootpath, "data", "subwaystations.geojson"))
df = pd.read_csv("/Users/chaupham/Downloads/MC2/VAST_MC2_2021/gps.csv")
print(df.shape)
df["Timestamp"] = pd.to_datetime(df["Timestamp"])
res_list = []
time_iterval = "5T" # 10mins
for i in df["id"].unique():
    tmp= df[df['id'] == i]
    tmp = tmp.resample(time_iterval, on='Timestamp').agg({'lat':'mean', 'long':'mean'}).reset_index().fillna(method = "ffill")#dropna()
    tmp["id"] = i
    res_list.append(tmp)


res_df= pd.concat(res_list) 
print(res_df.shape)
res_df.sort_values(["Timestamp", "id"], inplace=True)
print(df.shape[0]/res_df.shape[0])

res_df

(685169, 4)
(147068, 4)
4.658858487230397


Timestamp        lat       long  id
0    2014-01-06 06:25:00  36.072854  24.872431  35
0    2014-01-06 06:30:00  36.075658  24.869463   4
1    2014-01-06 06:30:00  36.067799  24.872222  35
1    2014-01-06 06:35:00  36.073336  24.865224   4
2    2014-01-06 06:35:00  36.067799  24.872222  35
...                  ...        ...        ...  ..
3899 2014-01-19 20:35:00  36.057323  24.902166  30
3900 2014-01-19 20:40:00  36.057323  24.902166  30
3901 2014-01-19 20:45:00  36.057323  24.902166  30
3902 2014-01-19 20:50:00  36.057323  24.902166  30
3903 2014-01-19 20:55:00  36.057235  24.902205  30

[147068 rows x 4 columns]

In [116]:
df.Timestamp.dt.date.min(), df.Timestamp.dt.date.max()

(datetime.date(2014, 1, 6), datetime.date(2014, 1, 19))

In [117]:
# df = pd.DataFrame([[1, 2, 3], [4, None, None], [None, None, 9]])
# df.fillna(method='ffill')
# df

In [118]:
gdf = gpd.GeoDataFrame(res_df, geometry=gpd.points_from_xy(res_df.long, res_df.lat))
gdf.set_crs(epsg=4326, inplace=True)
print(gdf.shape)
gdf.head()

(147068, 5)


Timestamp        lat       long  id                   geometry
0 2014-01-06 06:25:00  36.072854  24.872431  35  POINT (24.87243 36.07285)
0 2014-01-06 06:30:00  36.075658  24.869463   4  POINT (24.86946 36.07566)
1 2014-01-06 06:30:00  36.067799  24.872222  35  POINT (24.87222 36.06780)
1 2014-01-06 06:35:00  36.073336  24.865224   4  POINT (24.86522 36.07334)
2 2014-01-06 06:35:00  36.067799  24.872222  35  POINT (24.87222 36.06780)

In [119]:
import dill
with open(f"/Users/chaupham/Downloads/MC2/streamlit/gps_ffill_{time_iterval}.pkl", 'wb') as f:
    dill.dump(gdf, f)
    

In [120]:
# gdf['href'] = '<a href="' + gdf.url + '">' + gdf.url + "</a>"
# gdf['service_level'] = gdf.notes.str.split(', ').apply(lambda x: len([v for v in x if "all" in v]))
# gdf['lines_served'] = gdf.line.str.split('-').apply(lambda x: len(x))

In [29]:
# service_levels = gdf.service_level.unique().tolist()
# service_levels

In [30]:
colors =["#c51b7d",
"#de77ae",
"#f1b6da",
"#fde0ef",
"#f7f7f7",
"#e6f5d0",
"#b8e186",
"#7fbc41",
"#4d9221"]

colors = [
    'red',
    'blue',
    'gray',
    'darkred',
    'lightred',
    'orange',
    'beige',
    'green',
    'darkgreen',
    'lightgreen',
    'darkblue',
    'lightblue',
    'purple',
    'darkpurple',
    'pink',
    'cadetblue',
    'lightgray',
    'black'
]

# Use a Circle as a Marker

In [40]:
# m = folium.Map(location=[40.75, -73.95], zoom_start=13)

import json
with open("/Users/chaupham/Downloads/Abila.json", 'r') as j:
     contents = json.loads(j.read())
        
style1 = {'fillColor': 'gray', 'color': 'gray'}

lat, long = 36.07, 24.86
m = folium.Map([lat, long], zoom_start=14)

folium.GeoJson(contents, style_function=lambda x:style1).add_to(m)

m

In [104]:

def style_function(feature):
    props = feature.get('properties')
    markup = f"""
            <div style="font-size: 0.8em;">
            <div style="width: 10px;
                        height: 10px;
                        border: 1px solid {colors[props.get('id')%len(colors)] };
                        border-radius: 19px {colors[props.get('id')%len(colors)] };
                        background-color: {colors[props.get('id')%len(colors)] };">
            </div>
        </div>
        
    """
    return {"html": markup}





options = [4]
gps_filtered = gdf[gdf["id"].isin(options)]

folium.GeoJson(
    gps_filtered.drop(columns = ["Timestamp"]),
    name="Subway Stations",
    marker=folium.Circle(radius=30,  fill_opacity=0.5, weight=1, fill=True),
    tooltip=folium.GeoJsonTooltip(fields=["id"]),
    popup=folium.GeoJsonPopup(fields=["id"]),
#        style_function=style_function,
    style_function=lambda x: {
        "fillColor": colors[x['properties']['id']%len(colors)],
         "color":colors[x['properties']['id']%len(colors)]
#         "radius": (x['properties']['lines_served'])*30,
    },
    highlight_function=lambda x: {"fillOpacity": 0.8},
    zoom_on_click=True,                             
    

).add_to(m)

m.save("my_index.html")

In [105]:
import itertools
import folium.plugins as plugins
import json
def show_1_car_mutiple_day(car_id, gps):
    gps_filtered = gdf[gdf["id"] == car_id]
    gps_filtered = gps_filtered.sort_values(["Timestamp", "id"])
    all_dates = sorted(gps_filtered['Timestamp'].dt.date.unique())
    multi_list = list()
    for date in all_dates:
        tmp = gps_filtered[gps_filtered['Timestamp'].dt.date == date]
        multi =  list((tmp.groupby(["Timestamp"]).apply(lambda x: pd.DataFrame.to_numpy(x[["lat", "long"]]).tolist())))
        # multi[multi.index=="2014-01-07 12:10:00"]
        multi = list(itertools.chain(*multi))

        multi_list.append(multi)
        
  
    with open("/Users/chaupham/Downloads/Abila.json", 'r') as j:
         contents = json.loads(j.read())

    style1 = {'fillColor': 'gray', 'color': 'gray'}

    lat, long = 36.07, 24.86
    m = folium.Map([lat, long], zoom_start=14)

    folium.GeoJson(contents, style_function=lambda x:style1).add_to(m)

    weight = 1  # default value
    data = multi_list # multi #gps_filtered[["lat", "long"]].values
    index = list(map(str,all_dates)) #gps_filtered.Timestamp.astype(str).unique().tolist(),

    for time_entry in data:
        for row in time_entry:
            row.append(weight)

    hm = plugins.HeatMapWithTime( data, index =index,
                                 auto_play=True, max_opacity=0.9)

    hm.add_to(m)


    m.save("my_index.html")



In [107]:
import folium.plugins as plugins
import json
with open("/Users/chaupham/Downloads/Abila.json", 'r') as j:
     contents = json.loads(j.read())
        
style1 = {'fillColor': 'gray', 'color': 'gray'}

lat, long = 36.07, 24.86
m = folium.Map([lat, long], zoom_start=14)

folium.GeoJson(contents, style_function=lambda x:style1).add_to(m)

weight = 1  # default value
data = multi_list # multi #gps_filtered[["lat", "long"]].values
index = list(map(str,all_dates)) #gps_filtered.Timestamp.astype(str).unique().tolist(),

# data = data.reshape((-1,  1, 2)).tolist()

for time_entry in data:
    for row in time_entry:
        row.append(weight)

hm = plugins.HeatMapWithTime( data, index =index,
                             auto_play=True, max_opacity=0.9)

hm.add_to(m)




m.save("my_index.html")

In [108]:
!open my_index.html

## Or use a DivIcon

In [ ]:
m = folium.Map(location=[40.75, -73.95], zoom_start=13)


def style_function(feature):
    props = feature.get('properties')
    markup = f"""
        <a href="{props.get('url')}">
            <div style="font-size: 0.8em;">
            <div style="width: 10px;
                        height: 10px;
                        border: 1px solid black;
                        border-radius: 5px;
                        background-color: orange;">
            </div>
            {props.get('name')}
        </div>
        </a>
    """
    return {"html": markup}


folium.GeoJson(
    gdf,
    name="Subway Stations",
    marker=folium.Marker(icon=folium.DivIcon()),
    tooltip=folium.GeoJsonTooltip(fields=["name", "line", "notes"]),
    popup=folium.GeoJsonPopup(fields=["name", "line", "href", "notes"]),
    style_function=style_function,
    zoom_on_click=True,
).add_to(m)

m

## Use a Marker

In [ ]:
m = folium.Map(location=[40.75, -73.95], zoom_start=13)

marker_colors = ["red", "orange", "green", "blue"]

folium.GeoJson(
    gdf,
    name="Subway Stations",
    zoom_on_click=True,
    marker=folium.Marker(icon=folium.Icon(icon='star')),
    tooltip=folium.GeoJsonTooltip(fields=["name", "line", "notes"]),
    popup=folium.GeoJsonPopup(fields=["name", "line", "href", "notes"]),
    style_function=lambda x: {
        'markerColor': marker_colors[x['properties']['service_level']],
    },
).add_to(m)

m

In [271]:
style1 = {'fillColor': 'gray', 'color': 'gray'}

lat, long = 36.07, 24.86
m = folium.Map([lat, long], zoom_start=14)

folium.GeoJson(contents, style_function=lambda x:style1).add_to(m)
folium.raster_layers.ImageOverlay(
    image="/Users/chaupham/Downloads/MC2/VAST_MC2_2021/MC2-tourist.jpg",
    name="I am a jpeg",
    bounds=[[36.044, 24.822], [36.0958, 24.915]],
    opacity=0.5,
    interactive=False,
    cross_origin=False,
    zindex=1,
    alt="Wikipedia File:Mercator projection SW.jpg",
).add_to(m)

folium.LayerControl().add_to(m)


m

In [38]:
plugins.HeatMapWithTime?

In [113]:
from dateutil.relativedelta import relativedelta 

In [114]:
relativedelta?